* Añadir predictores: IDA1 y IDA2 del D-1; Perfil Solar Estandar
* Ampliar datos desde 2020
* Realizar transformaciones de variables

In [170]:
import pandas as pd
import numpy as np
import datetime as dt
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error, mean_squared_error
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV

import scipy.stats as stats
from sklearn.preprocessing import scale

### Preparación de datos

In [171]:
df_esios = pd.read_csv('data_training/esios_previsiones_d+1.csv')
df_esios['Date'] = pd.to_datetime(df_esios['Date']).dt.date

# Datetime de inicio del periodo
df_esios['Datetime'] = pd.to_datetime(df_esios['Date']) + pd.to_timedelta(df_esios['Hour'] - 1, unit='h')

df_esios

indicator_id        Date  Hour  geo_id     value            Datetime
0              1775  2023-01-01     1    8741  20059.80 2023-01-01 00:00:00
1              1775  2023-01-01     2    8741  19380.30 2023-01-01 01:00:00
2              1775  2023-01-01     3    8741  18523.80 2023-01-01 02:00:00
3              1775  2023-01-01     4    8741  17588.30 2023-01-01 03:00:00
4              1775  2023-01-01     5    8741  16834.50 2023-01-01 04:00:00
...             ...         ...   ...     ...       ...                 ...
87474           600  2025-06-30    20       3    111.38 2025-06-30 19:00:00
87475           600  2025-06-30    21       3    135.00 2025-06-30 20:00:00
87476           600  2025-06-30    22       3    175.01 2025-06-30 21:00:00
87477           600  2025-06-30    23       3    157.00 2025-06-30 22:00:00
87478           600  2025-06-30    24       3    127.86 2025-06-30 23:00:00

[87479 rows x 6 columns]

In [172]:
df_esios_clean = df_esios[['Datetime', 'indicator_id', 'value']].copy()
df_esios_clean.drop_duplicates(subset=['Datetime', 'indicator_id'], keep='first', inplace=True)

df_esios_pivot = df_esios_clean.pivot(
    index='Datetime',
    columns='indicator_id',
    values='value'
).reset_index()

df_esios_pivot

indicator_id            Datetime     600     1775     1777  1779
0            2023-01-01 00:00:00    0.00  20059.8  10266.8   0.0
1            2023-01-01 01:00:00    0.00  19380.3  10116.5   0.0
2            2023-01-01 02:00:00    0.00  18523.8   9954.0   0.0
3            2023-01-01 03:00:00    0.00  17588.3   9816.0   0.0
4            2023-01-01 04:00:00    0.00  16834.5   9625.5   0.0
...                          ...     ...      ...      ...   ...
21883        2025-06-30 19:00:00  111.38      NaN      NaN   NaN
21884        2025-06-30 20:00:00  135.00      NaN      NaN   NaN
21885        2025-06-30 21:00:00  175.01      NaN      NaN   NaN
21886        2025-06-30 22:00:00  157.00      NaN      NaN   NaN
21887        2025-06-30 23:00:00  127.86      NaN      NaN   NaN

[21888 rows x 5 columns]

In [173]:
df_input = df_esios_pivot.copy()

df_input['Year'] = df_input['Datetime'].dt.year
df_input['Month'] = df_input['Datetime'].dt.month
df_input['Day_of_Week'] = df_input['Datetime'].dt.dayofweek
df_input['Hour'] = df_input['Datetime'].dt.hour

dicc_indicators = {1775: 'demanda', 1777: 'gen_eolica', 1779: 'gen_fotovoltaica', 600: 'MD'}

df_input.rename(columns=dicc_indicators, inplace=True)


In [174]:
df_input['MD_lag_24'] = df_input['MD'].shift(24)
df_input['MD_lag_48'] = df_input['MD'].shift(48)

df_input['MD_lag_1w'] = df_input['MD'].shift(24*7)

df_input['hora_solar'] = np.where(
    df_input['gen_fotovoltaica'] == 0,
    0,
    1
)

df_input.index = df_input['Datetime']

df_input.drop(columns=['Datetime'], inplace=True)
df_input

indicator_id             MD  demanda  gen_eolica  gen_fotovoltaica  Year  \
Datetime                                                                   
2023-01-01 00:00:00    0.00  20059.8     10266.8               0.0  2023   
2023-01-01 01:00:00    0.00  19380.3     10116.5               0.0  2023   
2023-01-01 02:00:00    0.00  18523.8      9954.0               0.0  2023   
2023-01-01 03:00:00    0.00  17588.3      9816.0               0.0  2023   
2023-01-01 04:00:00    0.00  16834.5      9625.5               0.0  2023   
...                     ...      ...         ...               ...   ...   
2025-06-30 19:00:00  111.38      NaN         NaN               NaN  2025   
2025-06-30 20:00:00  135.00      NaN         NaN               NaN  2025   
2025-06-30 21:00:00  175.01      NaN         NaN               NaN  2025   
2025-06-30 22:00:00  157.00      NaN         NaN               NaN  2025   
2025-06-30 23:00:00  127.86      NaN         NaN               NaN  2025   

indicator_id         Month  Day_of_Week  Hour  MD_lag_24  MD_lag_48  \
Datetime                                                              
2023-01-01 00:00:00      1            6     0        NaN        NaN   
2023-01-01 01:00:00      1            6     1        NaN        NaN   
2023-01-01 02:00:00      1            6     2        NaN        NaN   
2023-01-01 03:00:00      1            6     3        NaN        NaN   
2023-01-01 04:00:00      1            6     4        NaN        NaN   
...                    ...          ...   ...        ...        ...   
2025-06-30 19:00:00      6            0    19     102.14      96.26   
2025-06-30 20:00:00      6            0    20     111.98     111.38   
2025-06-30 21:00:00      6            0    21     129.45     131.33   
2025-06-30 22:00:00      6            0    22     154.52     132.65   
2025-06-30 23:00:00      6            0    23     133.61     115.00   

indicator_id         MD_lag_1w  hora_solar  
Datetime                                    
2023-01-01 00:00:00        NaN           0  
2023-01-01 01:00:00        NaN           0  
2023-01-01 02:00:00        NaN           0  
2023-01-01 03:00:00        NaN           0  
2023-01-01 04:00:00        NaN           0  
...                        ...         ...  
2025-06-30 19:00:00     124.72           1  
2025-06-30 20:00:00     136.43           1  
2025-06-30 21:00:00     195.77           1  
2025-06-30 22:00:00     175.14           1  
2025-06-30 23:00:00     135.82           1  

[21888 rows x 12 columns]

### Limpieza de datos

In [175]:
df_input = df_input.dropna(axis=0)
df_input

indicator_id             MD  demanda  gen_eolica  gen_fotovoltaica  Year  \
Datetime                                                                   
2023-01-08 00:00:00    7.00  22622.3     14159.8               0.0  2023   
2023-01-08 01:00:00    5.00  20969.5     14112.8               0.0  2023   
2023-01-08 02:00:00    4.20  19781.5     13940.8               0.0  2023   
2023-01-08 03:00:00    4.16  19097.5     13824.5               0.0  2023   
2023-01-08 04:00:00    4.16  18748.3     13838.8               0.0  2023   
...                     ...      ...         ...               ...   ...   
2025-06-29 20:00:00  111.98  31241.5      4842.3            4534.8  2025   
2025-06-29 21:00:00  129.45  32164.5      4481.8             632.8  2025   
2025-06-29 22:00:00  154.52  32269.3      4226.0               0.0  2025   
2025-06-29 23:00:00  133.61  30043.3      3804.3               0.0  2025   
2025-06-30 00:00:00  125.50  28501.3      3794.0               0.0  2025   

indicator_id         Month  Day_of_Week  Hour  MD_lag_24  MD_lag_48  \
Datetime                                                              
2023-01-08 00:00:00      1            6     0      53.42     107.21   
2023-01-08 01:00:00      1            6     1      40.30     101.10   
2023-01-08 02:00:00      1            6     2      25.50      96.73   
2023-01-08 03:00:00      1            6     3      24.80      81.37   
2023-01-08 04:00:00      1            6     4      20.00      75.75   
...                    ...          ...   ...        ...        ...   
2025-06-29 20:00:00      6            6    20     111.38     116.83   
2025-06-29 21:00:00      6            6    21     131.33     141.05   
2025-06-29 22:00:00      6            6    22     132.65     138.56   
2025-06-29 23:00:00      6            6    23     115.00     115.31   
2025-06-30 00:00:00      6            0     0     111.38     112.96   

indicator_id         MD_lag_1w  hora_solar  
Datetime                                    
2023-01-08 00:00:00       0.00           0  
2023-01-08 01:00:00       0.00           0  
2023-01-08 02:00:00       0.00           0  
2023-01-08 03:00:00       0.00           0  
2023-01-08 04:00:00       0.00           0  
...                        ...         ...  
2025-06-29 20:00:00     114.12           1  
2025-06-29 21:00:00     128.76           1  
2025-06-29 22:00:00     130.78           0  
2025-06-29 23:00:00     128.76           0  
2025-06-30 00:00:00     127.73           0  

[21682 rows x 12 columns]

### Feature Engineering

In [176]:
# Creamos variables aleatorias para establecer un mínimo de influencia
df_input = df_input.copy()
df_input['rand1'] = np.random.uniform(0, 1, size=len(df_input))
df_input['rand2'] = np.random.uniform(0, 1, size=len(df_input))

In [178]:
df_predictores = df_input.drop(columns=['MD'])
variable_objetivo = df_input['MD']

Transformaciones numéricas de las variables

In [ ]:
# Transformaciones
# def cramers_v(var1, varObj): #Necesitamos que ambas variables sean nominales
    
#     #Tramificamos si las variables no son categoricas
#     if not var1.dtypes == 'category':
#         #bins = min(5,var1.value_counts().count())
#         var1 = pd.cut(var1, bins = 5)
#     if not varObj.dtypes == 'category': #np.issubdtype(varObj, np.number):
#         #bins = min(5,varObj.value_counts().count())
#         varObj = pd.cut(varObj, bins = 5)
	        
#     data = pd.crosstab(var1, varObj).values #Tabla cruzada de contingencia
#     vCramer = stats.contingency.association(data, method = 'cramer')
#     return vCramer

# def mejorTransf(vv, target, name=False, tipo = 'cramer', graf=False):
#     original_index = vv.index  # Store the original index

#     # Escalado de datos (evitar fallos de tamaño de float64 al hacer exp de número grande
#     vv = pd.Series(scale(vv), name=vv.name)
#     # Traslación a valores positivos de la variable (sino falla log y las raíces!)
#     vv = vv + abs(min(vv))+0.0001
      
#     # Definimos y calculamos las transformaciones típicas  
#     transf = pd.DataFrame({vv.name + '_ident': vv, vv.name + '_log': np.log(vv), 
# 												   vv.name + '_exp': np.exp(vv), vv.name + '_sqrt': np.sqrt(vv), 
# 	                         vv.name + '_sqr': np.square(vv), vv.name + '_cuarta': vv**4, 
# 	                         vv.name + '_raiz4': vv**(1/4)}, index=original_index)
      
#     # Distinguimos caso cramer o caso correlación
#     if tipo == 'cramer':
#       # Aplicar la función cramers_v a cada transformación frente a la respuesta
#       tablaCramer = pd.DataFrame(transf.apply(lambda x: cramers_v(x,target)),columns=['VCramer'])
      
#       # Si queremos gráfico, muestra comparativa entre las posibilidades
#       if graf: px.bar(tablaCramer,x=tablaCramer.VCramer,title='Relaciones frente a ' + target.name).update_yaxes(categoryorder="total ascending").show()
#       # Identificar mejor transformación
#       best = tablaCramer.query('VCramer == VCramer.max()').index
#       ser = transf[best[0]].squeeze()
    
#     if tipo == 'cor':
#       # Aplicar coeficiente de correlación a cada transformación frente a la respuesta
#       tablaCorr = pd.DataFrame(transf.apply(lambda x: np.corrcoef(x,target)[0,1]),columns=['Corr'])
#       # Si queremos gráfico, muestra comparativa entre las posibilidades
#       if graf: px.bar(tablaCorr,x=tablaCorr.Corr,title='Relaciones frente a ' + target.name).update_yaxes(categoryorder="total ascending").show()
#       # identificar mejor transformación
#       best = tablaCorr.query('Corr.abs() == Corr.abs().max()').index
#       ser = transf[best[0]].squeeze()
  
#     # Aquí distingue si se devuelve la variable transformada o solamente el nombre de la transformación
#     return ser.name if name else ser
    

# columnas_a_transformar = [col for col in df_predictores.columns if col != 'Datetime']

# # Aplicar mejorTransf solo a las columnas seleccionadas
# df_predictores_trans = df_predictores[columnas_a_transformar].apply(
#     lambda x: mejorTransf(x, variable_objetivo, tipo='cor')
# )
# transf_cramer_names = df_predictores[columnas_a_transformar].apply(lambda x: mejorTransf(x,variable_objetivo,tipo='cor', name=True))
# df_predictores_trans.columns = transf_cramer_names.values

# # Opcional: Si quieres mantener la columna Datetime en el resultado, haz un join
# df_predictores_trans['Datetime'] = df_predictores['Datetime'] 
# df_predictores_trans['Datetime'] = pd.to_datetime(df_predictores_trans['Datetime'])

# df_predictores_trans.set_index('Datetime', inplace=True)
# df_objetivo.set_index('Datetime', inplace=True)
# df_predictores_trans

demanda_sqr  gen_eolica_sqr  gen_fotovoltaica_sqr  \
Datetime                                                                 
2023-01-08 00:00:00     1.861883       11.412496          1.000000e-08   
2023-01-08 01:00:00     0.939772       11.334368          1.000000e-08   
2023-01-08 02:00:00     0.469822       11.050740          1.000000e-08   
2023-01-08 03:00:00     0.272411       10.860997          1.000000e-08   
2023-01-08 04:00:00     0.192244       10.884239          1.000000e-08   
...                          ...             ...                   ...   
2025-06-29 20:00:00    11.729704        1.170524          6.111016e-01   
2025-06-29 21:00:00    13.289684        0.986171          1.191832e-02   
2025-06-29 22:00:00    13.472964        0.864934          1.000000e-08   
2025-06-29 23:00:00     9.849834        0.682423          1.000000e-08   
2025-06-30 00:00:00     7.672017        0.678236          1.000000e-08   

                     Year_log     Month_sqr  Day_of_Week_cuarta   Hour_cuarta  \
Datetime                                                                        
2023-01-08 00:00:00 -9.210340  1.000000e-08        8.088979e+01  1.000000e-16   
2023-01-08 01:00:00 -9.210340  1.000000e-08        8.088979e+01  4.376340e-04   
2023-01-08 02:00:00 -9.210340  1.000000e-08        8.088979e+01  6.992466e-03   
2023-01-08 03:00:00 -9.210340  1.000000e-08        8.088979e+01  3.538304e-02   
2023-01-08 04:00:00 -9.210340  1.000000e-08        8.088979e+01  1.118021e-01   
...                       ...           ...                 ...           ...   
2025-06-29 20:00:00  0.986409  2.178606e+00        8.088979e+01  6.983765e+01   
2025-06-29 21:00:00  0.986409  2.178606e+00        8.088979e+01  8.488754e+01   
2025-06-29 22:00:00  0.986409  2.178606e+00        8.088979e+01  1.022480e+02   
2025-06-29 23:00:00  0.986409  2.178606e+00        8.088979e+01  1.221443e+02   
2025-06-30 00:00:00  0.986409  2.178606e+00        1.000000e-16  1.000000e-16   

                     MD_lag_24_ident  MD_lag_48_ident  MD_lag_1w_ident  \
Datetime                                                                 
2023-01-08 00:00:00         1.445855         2.583310         0.316664   
2023-01-08 01:00:00         1.168622         2.454160         0.316664   
2023-01-08 02:00:00         0.855889         2.361789         0.316664   
2023-01-08 03:00:00         0.841098         2.037118         0.316664   
2023-01-08 04:00:00         0.739671         1.918325         0.316664   
...                              ...              ...              ...   
2025-06-29 20:00:00         2.670584         2.786652         2.725080   
2025-06-29 21:00:00         3.092139         3.298602         3.034046   
2025-06-29 22:00:00         3.120032         3.245970         3.076676   
2025-06-29 23:00:00         2.747077         2.754523         3.034046   
2025-06-30 00:00:00         2.670584         2.704850         3.012309   

                     hora_solar_log  rand1_sqr  rand2_log  
Datetime                                                   
2023-01-08 00:00:00       -9.210340   9.851669  -0.456027  
2023-01-08 01:00:00       -9.210340   3.879060   0.778820  
2023-01-08 02:00:00       -9.210340  10.066543   0.215072  
2023-01-08 03:00:00       -9.210340   0.853487  -1.716629  
2023-01-08 04:00:00       -9.210340   1.322310   0.568580  
...                             ...        ...        ...  
2025-06-29 20:00:00        0.705045   0.808904  -0.345026  
2025-06-29 21:00:00        0.705045   0.480480   0.605220  
2025-06-29 22:00:00       -9.210340   8.042723  -0.493447  
2025-06-29 23:00:00       -9.210340   3.976296   0.518766  
2025-06-30 00:00:00       -9.210340   4.543954  -0.317594  

[21682 rows x 13 columns]

Análisis del comportamiento de las variables

In [179]:
def plot_target_vs_features_linear(var, target, df):
    proporcion = pd.DataFrame()
    proporcion['%'] = df[target].groupby(df[var]).mean() * 100
    proporcion['Conteo'] = df[target].groupby(df[var]).count()
    proporcion = proporcion.round(3)
    proporcion_filtered = proporcion[(proporcion['%'] > 0) & (proporcion['Conteo'] > 10)]
    
    if len(proporcion_filtered) < 100 and len(proporcion_filtered) > 1:
        fig = px.bar(proporcion_filtered, x=proporcion_filtered.index, y='Conteo', title=f'Distribución de {var}', labels={'x': var, 'Conteo': 'Cantidad'}, template='plotly_white')
        fig.add_trace(go.Scatter(x=proporcion_filtered.index, y=proporcion_filtered['%'], mode='lines+markers', name='%', yaxis='y2', line=dict(color='green')))
        
        fig.update_layout(
            yaxis2=dict(title='%', overlaying='y', side='right')
        )
    elif len(proporcion_filtered) >= 100:
        df_filtered = df[[var, target]].dropna()
        df_filtered['bin'] = pd.qcut(df_filtered[var], q=20, duplicates='drop')
        bin_means = df_filtered.groupby('bin')[target].mean() * 100
        bin_counts = df_filtered.groupby('bin')[target].count()
        
        fig = go.Figure()
        fig.add_trace(go.Bar(x=bin_means.index.astype(str), y=bin_counts, name='Conteo', yaxis='y', marker_color='blue'))
        fig.add_trace(go.Scatter(x=bin_means.index.astype(str), y=bin_means, mode='lines+markers', name='%', yaxis='y2', line=dict(color='green')))
        
        fig.update_layout(
            title=f'Relación entre {var} y {target}',
            xaxis_title=f'Binned {var}',
            yaxis=dict(title='Conteo'),
            yaxis2=dict(title='%', overlaying='y', side='right'),
            template='plotly_white'
        )
    else:
        proporcion_filtered.reset_index(inplace=True)
        fig = px.scatter(proporcion_filtered, x=var, y='%', trendline='ols', title=f'Relación entre {var} y % Depósitos', template='plotly_white')
    
    fig.show()


def plot_target_vs_features_linear(var, target, df):
    # Crear DataFrame con estadísticas para variables continuas
    grouped = df.groupby(var)[target].agg(['mean', 'count', 'median'])
    grouped.columns = ['Media', 'Conteo', 'Mediana']
    grouped = grouped.round(3)
    
    # Filtrar grupos con suficientes datos
    grouped_filtered = grouped[grouped['Conteo'] > 10]
    
    if len(grouped_filtered) < 100 and len(grouped_filtered) > 1:
        fig = go.Figure()
        
        # Gráfico de barras para conteo
        fig.add_trace(go.Bar(
            x=grouped_filtered.index,
            y=grouped_filtered['Conteo'],
            name='Conteo',
            marker_color='blue'
        ))
        
        # Línea para la media del target
        fig.add_trace(go.Scatter(
            x=grouped_filtered.index,
            y=grouped_filtered['Media'],
            mode='lines+markers',
            name='Media',
            yaxis='y2',
            line=dict(color='green')
        ))
        
        fig.update_layout(
            title=f'Relación entre {var} y {target}',
            xaxis_title=var,
            yaxis=dict(title='Conteo'),
            yaxis2=dict(
                title='Media Target',
                overlaying='y',
                side='right'
            ),
            template='plotly_white'
        )
    
    elif len(grouped_filtered) >= 100:
        # Crear bins para variables continuas con muchos valores únicos
        df_filtered = df[[var, target]].dropna()
        df_filtered['bin'] = pd.qcut(df_filtered[var], q=20, duplicates='drop')
        
        bin_stats = df_filtered.groupby('bin').agg({
            target: ['mean', 'count']
        })
        bin_stats.columns = ['Media', 'Conteo']
        
        fig = go.Figure()
        fig.add_trace(go.Bar(
            x=bin_stats.index.astype(str),
            y=bin_stats['Conteo'],
            name='Conteo',
            marker_color='blue'
        ))
        fig.add_trace(go.Scatter(
            x=bin_stats.index.astype(str),
            y=bin_stats['Media'],
            mode='lines+markers',
            name='Media',
            yaxis='y2',
            line=dict(color='green')
        ))
        
        fig.update_layout(
            title=f'Relación entre {var} y {target} (binned)',
            xaxis_title=f'Bins de {var}',
            yaxis=dict(title='Conteo'),
            yaxis2=dict(
                title='Media Target',
                overlaying='y',
                side='right'
            ),
            template='plotly_white'
        )
    
    else:
        # Gráfico de dispersión directo con línea de tendencia
        fig = px.scatter(
            df, 
            x=var, 
            y=target,
            trendline='ols',
            title=f'Relación entre {var} y {target}',
            template='plotly_white'
        )
    
    fig.show()

In [180]:
for i in [col for col in df_input.columns if col!='MD']:
    plot_target_vs_features_linear(i, 'MD', df)

C:\Users\jaime navarro\AppData\Local\Temp\ipykernel_4656\3037465215.py:86: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



C:\Users\jaime navarro\AppData\Local\Temp\ipykernel_4656\3037465215.py:86: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



C:\Users\jaime navarro\AppData\Local\Temp\ipykernel_4656\3037465215.py:86: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



### Split train - test

In [181]:
# Opcion 1: Aleatorio
X_train, X_test, y_train, y_test = train_test_split(
    df_predictores,
    variable_objetivo,
    test_size=0.2,
    random_state=8
)

# Opcion 2: Elegimos una fecha de separacion
split_date = dt.datetime(2025, 4, 30, 23, 0)
X = df_predictores
y = variable_objetivo
X_train, y_train = X[:split_date], y[:split_date]
X_test, y_test = X[split_date + dt.timedelta(hours=1):], y[split_date + dt.timedelta(hours=1):]

### Modelo Random Forest

In [182]:
model = RandomForestRegressor()
model.fit(X_train, y_train)

y_pred = model.predict(X_test)
print(f"MAE: {mean_absolute_error(y_test, y_pred):.2f}")
print(f"RMSE: {np.sqrt(mean_squared_error(y_test, y_pred)):.2f}")

MAE: 14.01
RMSE: 19.70


In [143]:
def plot_feature_importance(model, X_train):
    feat_importances = pd.DataFrame(model.feature_importances_, index=X_train.columns, columns=["Importance"])
    feat_importances.sort_values(by='Importance', ascending=False, inplace=True)
    
    fig = px.bar(feat_importances, x=feat_importances.index, y='Importance', title='Feature Importances', labels={'x': 'Features', 'Importance': 'Importance'}, template='plotly_white')
    fig.show()

    return feat_importances

plot_feature_importance(model, X_train)

Importance
indicator_id                
MD_lag_24           0.646105
gen_eolica          0.097366
MD_lag_1w           0.077080
demanda             0.041506
gen_fotovoltaica    0.035537
Day_of_Week         0.027538
MD_lag_48           0.023624
Month               0.017549
Year                0.008679
Hour                0.008441
rand2               0.008190
rand1               0.007778
hora_solar          0.000605

### Optimizacion de hiperparámetros

In [183]:
grid_param = {
    'n_estimators': [200, 250, 300],
    'max_depth': [5, 8, 10]
}

model = RandomForestRegressor()
model_grid = GridSearchCV(estimator=model, param_grid=grid_param, scoring='neg_mean_squared_error', cv=5, n_jobs=-1)

model_grid.fit(X_train, y_train)

print(model_grid.best_params_)
print(model_grid.best_score_) 

{'max_depth': 10, 'n_estimators': 250}
-448.23665230186964


In [185]:
best_model = model_grid.best_estimator_
y_pred = best_model.predict(X_test)

### Visualizacion de la predicción

In [186]:
y_comp_df = y_test.to_frame(name='y_test')
y_comp_df['y_pred'] = y_pred.round(2)
y_comp_df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 1441 entries, 2025-05-01 00:00:00 to 2025-06-30 00:00:00
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   y_test  1441 non-null   float64
 1   y_pred  1441 non-null   float64
dtypes: float64(2)
memory usage: 33.8 KB


In [188]:
px.line(y_comp_df[:(24*20)])